You need the following dependencies (and a SLURM cluster)
```python
conda install -c conda-forge kwant adaptive
pip install dask_jobqueue
```

In [ ]:
import adaptive
import kwant
import kwant.continuum
adaptive.notebook_extension()

In [ ]:
from dask_jobqueue import SLURMCluster
from dask.distributed import Client
cluster = SLURMCluster(threads=2, processes=16, memory='8GB',
                       death_timeout=600, env_extra=['export SYMPY_USE_CACHE=no'])
cluster.start_workers(10)
client = Client(cluster)

In [ ]:
client

In [ ]:
from functools import lru_cache
import kwant
import numpy as np

def get_template(a, subs={}):
    ham = ("(0.5 * hbar**2 * (k_x**2 + k_y**2 + k_z**2) / m_eff - mu + V) * kron(sigma_0, sigma_z) + "
           "alpha * (k_y * kron(sigma_x, sigma_z) - k_x * kron(sigma_y, sigma_z)) + "
           "0.5 * g * mu_B * (B_x * kron(sigma_x, sigma_0) + B_y * kron(sigma_y, sigma_0) + B_z * kron(sigma_z, sigma_0)) + "
           "Delta * kron(sigma_0, sigma_x)")
    template = kwant.continuum.discretize(ham, grid=a, locals=subs)
    return template

def get_shape(R, L):
    def shape(site):
        x, y, z = site.pos
        rsq = y**2 + z**2
        shape_yz = 0 <= rsq < R**2
        return (shape_yz and 0 <= x < L) if L > 0 else shape_yz
    return shape

# Use lru_cache such that the system is cached.
# @lru_cache()
def make_system(a, R, L):
    syst = kwant.Builder()

    sz = np.array([[1, 0], [0, -1]])
    cons_law = np.kron(np.eye(2), -sz)
    symmetry = kwant.TranslationalSymmetry((a, 0, 0))
    lead = kwant.Builder(symmetry, conservation_law=cons_law)
    lead2 = kwant.Builder(symmetry)

    syst.fill(get_template(a), get_shape(R, L), (0, 0, 0))

    lead_shape = get_shape(R, 0), (0, 0, 0)
    lead.fill(get_template(a, {'Delta': 0, 'V': 0}), *lead_shape)
    lead2.fill(get_template(a, {'V': 0}), *lead_shape)

    syst.attach_lead(lead)
    syst.attach_lead(lead2.reversed())
    return syst.finalized()


def andreev_conductance(syst, params, E):
    """The Andreev conductance is N - R_ee + R_he."""
    smatrix = kwant.smatrix(syst, energy=E, params=params)
    r_ee = smatrix.transmission((0, 0), (0, 0))
    r_he = smatrix.transmission((0, 1), (0, 0))
    N_e = smatrix.submatrix((0, 0), (0, 0)).shape[0]
    return N_e - r_ee + r_he

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt
syst = make_system(a=10, R=35, L=300)
kwant.plot(syst);

In [ ]:
def named_product(**items):
    from itertools import product
    names = items.keys()
    vals = items.values()
    return [dict(zip(names, res)) for res in product(*vals)]


def get_conductance(xy, val, params, syst_pars):    
    V_bias, params['B_x'] = xy
    params = dict(**params, **val)
    syst = make_system(**syst_pars)
    return andreev_conductance(syst, params, V_bias)

In [ ]:
import scipy.constants
from scipy.constants import physical_constants

# All constants int meV and nm.
constants = {'m_e': scipy.constants.m_e / scipy.constants.eV / (1e9)**2 * 1e3,
             'mu_B': physical_constants['Bohr magneton in eV/T'][0] * 1e3,
             'hbar': scipy.constants.hbar / scipy.constants.eV * 1e3}

constants['m_eff'] = 0.015 * constants['m_e']

In [ ]:
from functools import partial

def loss(ip):
    from adaptive.learner.learner2D import default_loss
    loss = default_loss(ip)
    if len(ip.values) < 400:
        loss *= 100
    return loss

params = dict(alpha=20, mu=12, B_y=0, B_z=0, g=50, Delta=0.250, V=30, **constants)  # The non changing parameters
syst_pars = dict(a=10, L=10, R=35)  # The system parameters

f = partial(get_conductance, val={}, params=params, syst_pars=syst_pars)
bounds = [(-params['Delta'], params['Delta']), (0, 4)]
learner = adaptive.Learner2D(f, bounds, loss_per_triangle=loss)

In [ ]:
runner = adaptive.Runner(learner, executor=client, goal=lambda l: l.loss() < 0.005, log=True)

In [ ]:
runner.live_info()

# WAIT UNTIL IT SAYS FAILED! and then run the next cell

In [ ]:
print(runner.task.print_stack())